#### 4.2 Stop right now, thank you very much
#### Objetivo: 
implemente uma estratégia de Parada Antecipada (Early Stopping) no
processo de treino da rede neural feita em Python puro ou no processo de treino da rede
neural feita em PyTorch




#### Construção da Rede Neural

A estratégia adotada para resolver este problema envolve a construção e treinamento de uma rede neural multicamadas (MLP - Multi-Layer Perceptron) para prever a temperatura com base nos dados de concentração de gases na atmosfera.

Foi implementada uma estratégia de early stopping utilizando um laço while. A lógica consiste em interromper o treinamento quando não houver melhora significativa na perda de validação por 5 épocas consecutivas. Isso é monitorado por uma variável, que é reiniciada sempre que há melhora, e incrementada caso contrário.

Esse método evita que a rede continue treinando após atingir seu melhor desempenho de generalização.

O processo de criação da MLP envolveu os seguintes passos:

1. **Leitura e Preparação dos Dados**:
   - Os dados são lidos de um arquivo CSV chamado `air_quality_modified.csv` utilizando o Pandas.
   - A variável de saída (`Temperature`) foi separada das variáveis de entrada (concentração dos gases).
   - Os dados foram divididos em três conjuntos: **treinamento**, **validação** e **teste**, utilizando a função `train_test_split` da biblioteca Scikit-Learn.

2. **Normalização dos Dados**:
   - Os dados de entrada foram normalizados utilizando o `StandardScaler` da biblioteca Scikit-Learn para garantir que todas as variáveis tenham uma média de 0 e desvio padrão de 1.


3. **Criação do Modelo MLP**:
   - Uma rede neural foi construída com duas camadas ocultas, usando a função de ativação **Sigmoid**. A estrutura do modelo foi definida para ter 64 neurônios na primeira camada oculta, 32 na segunda, e 1 neurônio na camada de saída, já que estamos prevendo um valor contínuo (temperatura).

4. **Treinamento e Ajuste do Modelo**:
   - O treinamento foi realizado com o otimizador **SGD** (Stochastic Gradient Descent) e a função de perda **MSELoss** (erro quadrático médio).
   - O processo de treinamento foi acompanhado pela validação a cada época, com a implementação de uma estratégia de **early stopping**: se a perda de validação não melhorasse por 5 épocas consecutivas, o treinamento seria interrompido antecipadamente para evitar overfitting.
---

#### Sobre o Dataset

O **dataset** utilizado contém dados sobre a qualidade do ar, com informações sobre a concentração de diversos **gases atmosféricos** e a **temperatura**. Os dados de entrada consistem em várias características relacionadas aos gases, como CO, NO2, O3, etc., enquanto a variável alvo (ou saída) é a **temperatura**.

A **previsão da temperatura** foi feita com base nos níveis de gases presentes na atmosfera, utilizando os dados históricos para treinar o modelo e ajustar os parâmetros da rede neural. O modelo tenta entender a relação entre a quantidade desses gases e a temperatura para prever o valor da temperatura em novos conjuntos de dados.


In [53]:
import pandas as pd

df = pd.read_csv("air_quality_modified.csv")


df

PM10        NO2        SO2        VOCs        CO         CO2  \
0     57.926035  55.230299   4.531693   75.317261  2.789606  427.674347   
1    150.774299  79.051618  18.744780  145.083987  1.966569  529.739619   
2    138.948796  60.466604  14.892239  145.147338  2.626446  499.889443   
3     63.643900  15.333286   7.647429  130.022319  1.779360  388.283712   
4    113.977926  59.202337  17.696806  181.713667  3.240533  464.739197   
..          ...        ...        ...         ...       ...         ...   
495   57.573550  19.276010  11.167098  104.071502  1.844483  397.418878   
496   75.372133  18.535162  12.169426   74.802208  1.364096  392.316075   
497   88.097250  15.653370   7.997326  128.105470  2.319453  378.653347   
498   40.847991  19.365916   7.218154  106.053329  1.599748  389.878566   
499   34.287210   5.122962   7.415822   93.332250  1.633200  388.029985   

          CH4  Temperature  
0    1.706105    31.085120  
1    2.492663    33.711103  
2    2.431165    33.778698  
3    1.818563    31.565877  
4    2.597225    32.229835  
..        ...          ...  
495  1.923525    34.323410  
496  2.157281    26.321361  
497  1.809489    28.964494  
498  1.858964    29.976442  
499  2.059903    26.649351  

[500 rows x 8 columns]

In [54]:
import torch
import torch.nn as nn
import torch.optim as optim
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import mean_squared_error
import numpy as np

class MLP(nn.Module):
    def __init__(self, num_dados_entrada, neuronios_c1, neuronios_c2, num_targets):
        super().__init__()
        
        self.camadas = nn.Sequential(
            nn.Linear(num_dados_entrada, neuronios_c1),
            nn.Sigmoid(),
            nn.Linear(neuronios_c1, neuronios_c2),
            nn.Sigmoid(),
            nn.Linear(neuronios_c2, num_targets),
        )
        
    def forward(self, x):
        x = self.camadas(x)
        return x

In [55]:
# 1. Separar as variáveis de entrada e saída
entradas = df.drop(columns=["Temperature"]).values
saidas = df["Temperature"].values.reshape(-1, 1)

# Dividir os dados em treino, validação e teste
entradas_temp, entradas_teste, saidas_temp, saidas_teste = train_test_split(
    entradas, saidas, test_size=0.1, random_state=36)

entradas_treino, entradas_val, saidas_treino, saidas_val = train_test_split(
    entradas_temp, saidas_temp, test_size=0.1, random_state=36)

# 2. Normalizar os dados
scaler = StandardScaler()

# Ajustar o scaler nos dados de treino e transformar todos os dados (treino, validação, teste)
entradas_treino_scaled = scaler.fit_transform(entradas_treino)
entradas_val_scaled = scaler.transform(entradas_val)
entradas_teste_scaled = scaler.transform(entradas_teste)

# 3. Converter para tensores PyTorch
entradas_treino_tensor = torch.tensor(entradas_treino_scaled, dtype=torch.float32)
saidas_treino_tensor = torch.tensor(saidas_treino, dtype=torch.float32).view(-1, 1)

entradas_val_tensor = torch.tensor(entradas_val_scaled, dtype=torch.float32)
saidas_val_tensor = torch.tensor(saidas_val, dtype=torch.float32).view(-1, 1)

entradas_teste_tensor = torch.tensor(entradas_teste_scaled, dtype=torch.float32)
saidas_teste_tensor = torch.tensor(saidas_teste, dtype=torch.float32).view(-1, 1)


# 1. Separar as variáveis de entrada e saída
entradas = df.drop(columns=["Temperature"]).values
saidas = df["Temperature"].values.reshape(-1, 1)

# Dividir os dados em treino, validação e teste
entradas_temp, entradas_teste, saidas_temp, saidas_teste = train_test_split(
    entradas, saidas, test_size=0.1, random_state=36)

entradas_treino, entradas_val, saidas_treino, saidas_val = train_test_split(
    entradas_temp, saidas_temp, test_size=0.1, random_state=36)

# 2. Normalizar os dados
scaler = StandardScaler()

# Ajustar o scaler nos dados de treino e transformar todos os dados (treino, validação, teste)
entradas_treino_scaled = scaler.fit_transform(entradas_treino)
entradas_val_scaled = scaler.transform(entradas_val)
entradas_teste_scaled = scaler.transform(entradas_teste)

# 3. Converter para tensores PyTorch
entradas_treino_tensor = torch.tensor(entradas_treino_scaled, dtype=torch.float32)
saidas_treino_tensor = torch.tensor(saidas_treino, dtype=torch.float32).view(-1, 1)

entradas_val_tensor = torch.tensor(entradas_val_scaled, dtype=torch.float32)
saidas_val_tensor = torch.tensor(saidas_val, dtype=torch.float32).view(-1, 1)

entradas_teste_tensor = torch.tensor(entradas_teste_scaled, dtype=torch.float32)
saidas_teste_tensor = torch.tensor(saidas_teste, dtype=torch.float32).view(-1, 1)


In [56]:
NUM_DADOS_DE_ENTRADA = entradas_treino.shape[1] 
NUM_DADOS_DE_SAIDA = 1  # Porque temos uma variável de saída (Temperatura)
NEURONIOS_C1 = 64  # Número de neurônios na primeira camada oculta
NEURONIOS_C2 = 32  # Número de neurônios na segunda camada oculta

minha_mlp = MLP(
    NUM_DADOS_DE_ENTRADA, NEURONIOS_C1, NEURONIOS_C2, NUM_DADOS_DE_SAIDA
)


In [57]:
# Configurando a taxa de aprendizado e o otimizador (SGD)
TAXA_DE_APRENDIZADO = 0.001
otimizador = optim.SGD(minha_mlp.parameters(), lr=TAXA_DE_APRENDIZADO)

# Função de perda (erro quadrático médio)
fn_perda = nn.MSELoss()


In [58]:
contador_epocas = 0
epoca = 1
perda_anterior = float("inf")

while(contador_epocas < 5 or epoca >= 1000000):

    # Zerar os gradientes do otimizador
    otimizador.zero_grad()

    # Passagem para frente: calcular as previsões da rede
    y_pred = minha_mlp(entradas_treino_tensor)
    
    # Calcular a perda
    perda_treino = fn_perda(y_pred, saidas_treino_tensor)
    
    # Calcular a perda de validação
    y_pred_validacao = minha_mlp(entradas_val_tensor)
    perda_validacao = fn_perda(y_pred_validacao, saidas_val_tensor)
    
    # Backpropagation: calcular os gradientes
    perda_treino.backward()

    # Atualizar os pesos
    otimizador.step()
    
    print(f"Época {epoca}, Perda treino: {perda_treino.item()}, Perda validação: {perda_validacao.item()}")

    if perda_validacao >= perda_anterior:
        contador_epocas += 1
    else: contador_epocas = 0
    
    perda_anterior = perda_validacao
    epoca += 1


Época 1, Perda treino: 945.5360107421875, Perda validação: 946.01708984375
Época 2, Perda treino: 911.4867553710938, Perda validação: 911.9224853515625
Época 3, Perda treino: 878.493896484375, Perda validação: 878.8853149414062
Época 4, Perda treino: 846.1161499023438, Perda validação: 846.4637451171875
Época 5, Perda treino: 813.9978637695312, Perda validação: 814.3014526367188
Época 6, Perda treino: 781.8607788085938, Perda validação: 782.1198120117188
Época 7, Perda treino: 749.4992065429688, Perda validação: 749.7125854492188
Época 8, Perda treino: 716.7776489257812, Perda validação: 716.944091796875
Época 9, Perda treino: 683.6286010742188, Perda validação: 683.7466430664062
Época 10, Perda treino: 650.0509033203125, Perda validação: 650.1187744140625
Época 11, Perda treino: 616.1051635742188, Perda validação: 616.1212768554688
Época 12, Perda treino: 581.9078979492188, Perda validação: 581.8707275390625
Época 13, Perda treino: 547.6224365234375, Perda validação: 547.5303955078125

In [60]:
print(f"Parada antecipada após {epoca} épocas.")
print(f"Valor final de perda de validação: {perda_validacao.item()}")

Parada antecipada após 52411 épocas.
Valor final de perda de validação: 4.080187797546387


In [61]:
# Obter as previsões da rede usando as entradas de teste
y_pred_teste = minha_mlp(entradas_teste_tensor)

# Calcular o erro quadrático médio no conjunto de teste
erro_teste = fn_perda(y_pred_teste, saidas_teste_tensor)

print(f"Erro quadrático médio no conjunto de teste: {erro_teste.item()}")


Erro quadrático médio no conjunto de teste: 4.013908386230469


#### Conclusão: Funcionamento do Loop `while` e Prevenção de Overfitting

O loop `while` implementado no código tem como objetivo controlar o treinamento da rede neural de forma a prevenir o **overfitting**. A lógica de parada antecipada funciona da seguinte maneira:

1. **Contagem de Épocas Sem Melhora**:
   - O loop executa o treinamento por múltiplas épocas, mas a cada iteração ele verifica se a **perda de validação** está aumentando em relação à época anterior.
   - Se a perda de validação não melhorar (ou seja, se ela aumentar ou permanecer constante), o contador `contador_epocas` é incrementado.

2. **Parada Antecipada**:
   - Se o contador de épocas sem melhora atingir o limite de 5 (definido como critério de paciência), o treinamento é interrompido.
   - Isso ajuda a evitar que o modelo continue a treinar e ajuste demais seus parâmetros para os dados de treinamento, prevenindo o **overfitting** e garantindo que o modelo não se torne excessivamente ajustado a ruídos nos dados.

3. **Exibição do Resultado**:
   - Quando o treinamento é interrompido, o código imprime em qual época o modelo parou e qual foi o valor final da perda de validação. 

Essa abordagem de **early stopping** ajuda a otimizar o processo de treinamento, evitando o sobreajuste e garantindo que o modelo se generalize bem para novos dados.


#### Referências

ATP-303 NN 5.2 - Notebook PyTorch - Dr. Daniel Roberto Cassar